In [1]:
from copy import deepcopy
from math import log
import queue  # 用来层序打印决策树
import time  # 用来记录运行时间

In [ ]:
TRAIN_DATA='./data1/adult.data'
CLEAN_DATA='./data1/adult_clean.data'
TEST_DATA='./data1/adult.test'

In [2]:
class TreeNode():
    def __init__(self, attributeIndex, attributeValue=None, isContinue=False, threshold=None):
        self.attributeIndex: int = attributeIndex
        self.attributeValue: str = attributeValue  # 离散属性值
        self.childs = []
        self.isLeaf = False
        self.label = ''
        self.isContinue = isContinue
        self.threshold: int = threshold  # 连续属性划分值

In [3]:
def CleanData():
    with open(TRAIN_DATA, 'r') as f:
        with open(CLEAN_DATA, 'w') as output:
            for line in f:
                if line == '\n':
                    continue
                if '?' in line:
                    continue
                # words = Line(line)
                words = line.split(',')
                for word in words[:-2]:
                    output.write(word)
                output.write(words[-1])

In [4]:
CleanData()

In [5]:
# 读取训练集
data = open(CLEAN_DATA, 'r')
lines = data.readlines()

In [6]:
# 读取数据，去掉换行
Labels = []
sampleIndex = []  # 0-30161
for i in range(len(lines)):
    sampleIndex.append(i)
    lines[i] = lines[i].strip('\n')
    if (lines[i].split(' ')[-1] == '<=50K'):
        Labels.append(0)
    else:
        Labels.append(1)

# 最后一行会有空行
lines = lines[:-1]
sampleIndex = sampleIndex[:-1]

allAttributesIndex = []  # 0-13
for i in range(len(lines[0].split(' '))):
    allAttributesIndex.append(i)
allAttributesIndex = allAttributesIndex[:-1]
continueAttributeIndex = [0, 4, 10, 11, 12]  # 若2作为连续值，计算量太大，需要加速计算，在生成树函数中体现, 不使用性能较好，使用的话可以在数组里添加2，使用2准确率为64%，非常慢 
discreteAttributeIndex = [1, 3, 5, 6, 7, 8, 9]  # 12 为离散值的时候可能会出现没有出现过的值，所以作为连续值比较好

In [7]:
def MostLabel(sample: list):
    """
    选出sample中最多的类别
    :param sample: sample 索引
    :return: 类别
    """
    positive = 0
    negtive = 0
    for i in sample:
        if (Labels[i] == '<=50K'):
            negtive += 1
        else:
            positive += 1
    if positive > negtive:
        return '1'
    else:
        return '0'

In [8]:
def CreateDicisionTree(samplesIndex: list, discreteAttributeIndex: list, continueAttributeIndex: list,
                       root: TreeNode = None, deep: int = 0, reUse: bool = True):
    """
    生成一棵 DicisionTree
    :param samplesIndex: 结点的数据索引
    :param discreteAttributeIndex: 离散的属性索引
    :param continueAttributeIndex: 连续属性索引
    :param root: 当前结点
    :return: None 创建时传入一个头节点，生成以该结点为根节点的DecisionTree
    """
    # 减枝
    # if (len(samplesIndex) < 10):   # 这种方法效果不好
    #     root.isLeaf = True
    #     root.label = MostLabel(samplesIndex)
    #     return
    if (reUse and deep > 20):
        root.isLeaf = True
        root.label = MostLabel(samplesIndex)
        return
    if (discreteAttributeIndex == []):
        root.isLeaf = True
        root.label = MostLabel(samplesIndex)
        return
    isSame = True
    l = Labels[samplesIndex[0]]
    for i in samplesIndex:
        if Labels[i] != l:
            isSame = False
            break
    if isSame:
        root.label = l
        root.isLeaf = True
        return
    # 一个存储 Sample 的 dict
    # 第一个索引为attribute 的编号 int
    # 第二个索引为attribute 所有的取值，连续的多一个记录 ['min_ent']
    # 第三个索引连续值和离散值不同
    # 离散{'positive':0,'negtive':0，'sample':[]}
    # 连续{'sample':sample_index,'label':int(flag)}
    dict_attribute_index_attribute_class = []
    # 计算所有属性的Ent，以及每个属性对应的sample index
    for i in range(len(allAttributesIndex)):
        dict_attribute_index_attribute_class.append({})

    for i in samplesIndex:
        flag = 0
        if (Labels[i]):
            flag = 1
        attributes = lines[i].split(' ')
        # print(attributes)
        # 计算离散属性的Ent
        # 离散 map 数据结构
        # index:{'name':{'positive':0,'negtive':0，'sample':[]}，... , }
        for j in discreteAttributeIndex:
            if (dict_attribute_index_attribute_class[j].get(attributes[j])):
                if (flag):
                    dict_attribute_index_attribute_class[j][attributes[j]]['positive'] += 1
                    dict_attribute_index_attribute_class[j][attributes[j]]['sample'].append(i)
                else:
                    dict_attribute_index_attribute_class[j][attributes[j]]['negtive'] += 1
                    dict_attribute_index_attribute_class[j][attributes[j]]['sample'].append(i)
            else:
                if (flag):
                    dict_attribute_index_attribute_class[j][attributes[j]] = {'positive': 1, 'negtive': 0,
                                                                              'sample': [i]}
                else:
                    dict_attribute_index_attribute_class[j][attributes[j]] = {'positive': 0, 'negtive': 1,
                                                                              'sample': [i]}
        # 连续值处理
        # 连续值 map 数据结构
        # index:{ value:{'sample':sample_index,'label':int(flag)} }
        for j in continueAttributeIndex:
            # 需要用到的东西，每个属性的总样本量，以及里面的正负样本
            if (dict_attribute_index_attribute_class[j].get(int(attributes[j]))):
                if flag:
                    dict_attribute_index_attribute_class[j][int(attributes[j])]['positive'] += 1
                    dict_attribute_index_attribute_class[j][int(attributes[j])]['sample'][i] = flag
                else:
                    dict_attribute_index_attribute_class[j][int(attributes[j])]['negtive'] += 1
                    dict_attribute_index_attribute_class[j][int(attributes[j])]['sample'][i] = flag
            else:
                if flag:
                    dict_attribute_index_attribute_class[j][int(attributes[j])] = {'sample': {i: flag}, 'positive': 1,
                                                                                   'negtive': 0}
                else:
                    dict_attribute_index_attribute_class[j][int(attributes[j])] = {'sample': {i: flag}, 'positive': 0,
                                                                                   'negtive': 1}

    # 计算连续属性最小Ent
    for j in continueAttributeIndex:
        dict_attribute_index_attribute_class[j]['min_ent'] = (999, 99999)  # Ent curValue
        key_sorted = sorted(list(dict_attribute_index_attribute_class[j].keys())[:-1])
        # 选出Ent最小的划分
        for i in range(0, len(key_sorted) - 1):
            # 取出当前的划分
            # 这里取得是Value
            cur_value = float((key_sorted[i] + key_sorted[i + 1]) / 2)
            front_negtive = 0
            front_positve = 0
            l = 0
            while (l < len(key_sorted) and key_sorted[l] < cur_value):
                # 找到Value 对应的sample index   # 找到的sample 太少了
                # 计算属性值小于这个的Ent
                front_negtive += dict_attribute_index_attribute_class[j][key_sorted[l]]['negtive']
                front_positve += dict_attribute_index_attribute_class[j][key_sorted[l]]['positive']
                # l+=1
                # 加速第三个属性计算
                if (j == 2):
                    l += 10
                else:
                    l += 1

            front_num = front_positve + front_negtive
            # 要记录当前的值和index
            if (front_positve == 0):
                front = 0
            else:
                front = -(front_positve / (front_positve + front_negtive) * log(
                    front_positve / (front_positve + front_negtive)))
            if (front_negtive == 0):
                later = 0
            else:
                later = - (front_negtive / (front_positve + front_negtive) * log(
                    front_negtive / (front_positve + front_negtive)))
            front_ent = front + later

            later_negtive = 0
            later_positve = 0
            l = -1
            while (l >= -len(key_sorted) and key_sorted[l] >= cur_value):
                later_negtive += dict_attribute_index_attribute_class[j][key_sorted[l]]['negtive']
                later_positve += dict_attribute_index_attribute_class[j][key_sorted[l]]['positive']
                # l-=1
                # 加速第三个属性计算
                if (j == 2):
                    l -= 10
                else:
                    l -= 1
            later_num = later_positve + later_negtive
            # 要记录当前的值和index
            if (later_positve == 0):
                front = 0
            else:
                front = -(later_positve / (later_positve + later_negtive) * log(
                    later_positve / (later_positve + later_negtive)))
            if (later_negtive == 0):
                later = 0
            else:
                later = - (later_negtive / (later_positve + later_negtive) * log(
                    later_negtive / (later_positve + later_negtive)))
            later_ent = front + later
            # 计算加权Ent，要选出最小的Ent
            ENT = (front_num / (front_num + later_num)) * front_ent + (later_num / (front_num + later_num)) * later_ent
            if ENT < dict_attribute_index_attribute_class[j]['min_ent'][0]:
                dict_attribute_index_attribute_class[j]['min_ent'] = (ENT, cur_value)
            # 加速第三个属性计算
            if (j == 2):
                i += 100
            # Ent ContinueAttributeIndex cur_value

    # 计算离散属性Ent以及选择最小Ent属性
    is_continue = False
    min_index = 999999
    min_ent = 999999
    discreteAttri = []
    for i in allAttributesIndex:
        if i in discreteAttributeIndex:
            if (dict_attribute_index_attribute_class[i] == {}):
                continue
            else:
                ent, weight_ent = Ent(dict_attribute_index_attribute_class[i])
                discreteAttri.append(weight_ent)
                if weight_ent < min_ent:
                    min_ent = weight_ent
                    min_index = i
                    is_continue = False
        if i in continueAttributeIndex:
            discreteAttri.append(999999)
            if dict_attribute_index_attribute_class[i]['min_ent'][0] < min_ent:
                min_ent = dict_attribute_index_attribute_class[i]['min_ent'][0]
                min_index = i
                is_continue = True

    # 选出weight_ent 最小的一个属性当作结点
    # 要从当前的属性索引列表中去掉这个属性索引，再进行子节点构建
    # 要判断是否为连续的属性
    node_attri_index = min_index

    # print('Node', node_attri_index)
    front_index = []
    later_index = []

    if is_continue:
        # 如果是连续的话，还需要知道前后的索引
        # 计算前后索引
        key_sorted = sorted(list(dict_attribute_index_attribute_class[node_attri_index].keys())[:-1])
        l = 0
        while (l < len(key_sorted) and key_sorted[l] <
               dict_attribute_index_attribute_class[node_attri_index]['min_ent'][1]):
            front_index += dict_attribute_index_attribute_class[node_attri_index][key_sorted[l]]['sample']
            l += 1
        l = -1
        while (l >= -len(key_sorted) and key_sorted[l] >=
               dict_attribute_index_attribute_class[node_attri_index]['min_ent'][1]):
            later_index += dict_attribute_index_attribute_class[node_attri_index][key_sorted[l]]['sample']
            l -= 1

    # 不是连续值
    if not is_continue:
        for key in dict_attribute_index_attribute_class[node_attri_index]:
            root.childs.append(TreeNode(attributeIndex=node_attri_index, attributeValue=key))
        for i in root.childs:
            temp = deepcopy(discreteAttributeIndex)
            # 离散值只分类一次，要去掉离散索引
            temp.remove(node_attri_index)
            CreateDicisionTree(dict_attribute_index_attribute_class[i.attributeIndex][i.attributeValue]['sample'], temp,
                               continueAttributeIndex, i, deep=deep + 1, reUse=reUse)
    else:
        if (front_index != [] and later_index != []):
            # 是否重复使用连续属性
            if reUse:
                temp = continueAttributeIndex
            else:
                temp = deepcopy(continueAttributeIndex)
                temp.remove(node_attri_index)
            # 使用二分法
            for i in range(2):
                root.childs.append(
                    TreeNode(attributeIndex=node_attri_index, isContinue=True,
                             threshold=dict_attribute_index_attribute_class[node_attri_index]['min_ent'][1]))
            for i in range(2):
                # 取得先后的索引
                # 离散和连续的属性索引不变
                if i == 0:  # 小于的时候
                    CreateDicisionTree(front_index, discreteAttributeIndex, temp, root.childs[i],
                                       deep=deep + 1, reUse=reUse)
                else:
                    CreateDicisionTree(later_index, discreteAttributeIndex, temp, root.childs[i],
                                       deep=deep + 1, reUse=reUse)
        else:
            # 如果都为空，说明属性相同，直接设置即可
            root.isLeaf = True
            root.label = MostLabel(samplesIndex)

In [9]:
def Ent(attribute: dict):
    all = 0
    classNum = []
    subEnt = []
    # 各个属性的Ent
    for key in attribute:
        positive = attribute[key]['positive']
        negtive = attribute[key]['negtive']
        if (positive == 0):
            front = 0
        else:
            front = -(positive / (positive + negtive) * log(positive / (positive + negtive)))
        if (negtive == 0):
            later = 0
        else:
            later = - (negtive / (positive + negtive) * log(negtive / (positive + negtive)))
        ent = front + later
        subEnt.append(ent)
        classNum.append(positive + negtive)
    # 统计总量
    for i in classNum:
        all += i
    # 加权Ent
    weightEnt = 0
    entIndex = 0
    for key in attribute:
        belong_num = attribute[key]['positive'] + attribute[key]['negtive']
        weightEnt += (belong_num / all) * subEnt[entIndex]
        entIndex += 1
    return subEnt, weightEnt

In [10]:
# 测试
def Test(line):
    cur_node = deepcopy(root)
    words = line.split(',')
    for i in range(len(words)):
        words[i] = words[i].strip(' ')
    print(words)
    while (cur_node.isLeaf != True):
        # 在这里需要判断是否是连续的属性变量
        attribute_id = cur_node.childs[0].attributeIndex
        cur_attribute = words[attribute_id]
        if attribute_id in discreteAttributeIndex:
            find = False
            for i in cur_node.childs:
                if i.attributeValue == cur_attribute:
                    cur_node = i
                    find = True
                    break
            # 无法分类的时候
            if (not find):
                return '0', False;
        else:
            # 变为数字
            cur_attribute = int(cur_attribute)
            nodeAttribute = cur_node.childs[0].threshold
            if cur_attribute <= nodeAttribute:
                cur_node = cur_node.childs[0]
            else:
                cur_node = cur_node.childs[1]
    pred = False
    if (words[-1] == '>50K' and cur_node.label == 1) or (words[-1] == '<=50K' and cur_node.label == 0):
        pred = True
    return cur_node.label, pred

In [11]:
def printTree(root):
    q = queue.Queue()
    q.put(root)
    while (not q.empty()):
        size = q.qsize()
        while (size):
            size -= 1
            cur = q.get()
            if (cur == '|'):
                print(cur, end='')
                continue
            print(cur.attributeIndex, end=' ')
            for i in cur.childs:
                q.put(i)
            q.put('|')
        print('\n')

In [12]:
if __name__ == '__main__':
    # 训练集读取在程序开头
    # 构建DecisionTree
    time_start = time.time()
    root = TreeNode(attributeIndex=-1, attributeValue='root')
    CreateDicisionTree(sampleIndex, discreteAttributeIndex, continueAttributeIndex, root)
    time_end_1 = time.time()
    time_sum = time_end_1 - time_start
    print('构造树的时间', time_sum)
    # 打印树结点信息
    printTree(root)
    # 测试数据集
    data = open(TEST_DATA, 'r')
    # 测试集第一行会有一行不是数据，从文件中删掉后不需要这句
    data.readline()
    right = 0
    all = 0
    no = 0

    time_start_all = time.time()
    for line in data:
        time_start = time.time()
        if '?' in line:
            continue
        # 数据集最后有空行
        if len(line) < 20:
            continue
        line = line.strip('\n')
        line = line.strip('.')
        res, pred = Test(line)
        if pred:
            right += 1
        all += 1
        time_end_1 = time.time() 
        time_sum = time_end_1 - time_start  
        print('time:', time_sum, 's')
        print('acc:', (right / all) * 100, '%')
        print('进度:', no * 100 / 15060, '%')
        no += 1

    time_end_1 = time.time()  
    time_sum = time_end_1 - time_start_all 
    print('FINISH! \n', (right / all) * 100, '%')

构造树的时间 2.0304341316223145
-1 

7 7 7 7 7 7 |

10 10 |3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 |6 6 6 6 6 6 6 6 6 6 6 6 6 |10 10 |10 10 |6 6 6 6 6 6 6 6 6 6 6 6 6 6 |

3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 |1 1 1 1 1 1 |10 10 |10 10 |10 10 |10 10 |6 6 6 6 6 6 6 6 6 6 6 6 |10 10 |12 12 |10 10 |10 10 |10 10 |6 6 6 6 6 6 6 6 6 6 6 6 6 |10 10 |6 6 6 6 6 6 6 6 6 6 6 6 |6 6 6 6 6 6 6 6 6 |6 6 6 6 6 6 6 6 6 6 6 6 6 ||10 10 |3 3 3 3 3 3 3 3 3 3 3 |10 10 |3 3 3 3 3 3 3 3 3 3 3 3 |10 10 |3 3 3 3 3 3 3 3 3 |10 10 |10 10 |3 3 3 3 3 3 3 ||3 3 3 3 3 3 ||3 3 3 3 3 |5 5 5 5 5 5 5 |0 0 |3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 |6 6 6 6 6 6 6 6 6 6 |10 10 |8 8 8 8 8 |5 5 5 |1 1 1 1 1 ||1 1 1 1 |0 0 ||5 5 5 5 5 5 |1 1 |||3 3 3 3 3 3 3 3 3 3 ||

6 6 6 6 6 6 6 6 6 6 6 6 6 6 |6 6 6 6 6 6 6 6 6 6 6 6 |6 6 6 6 6 6 6 6 6 6 6 6 6 |6 6 6 6 6 6 6 6 6 6 6 6 6 |0 0 |0 0 |6 6 6 6 6 |6 6 6 6 6 6 6 6 6 6 6 |11 11 ||0 0 |6 6 6 6 6 6 6 6 6 6 6 |12 12 ||12 12 |||12 12 |||||11 11 |0 0 |12 12 |12 12 |6 6 6 6 6 6 6 6 6 6 6 6 |0 0 |6 6 6 6 6 6 6 6 6

|||0 0 |||||0 0 |0 0 |12 12 ||0 0 ||1 1 1 |0 0 |||0 0 |0 0 |||12 12 ||||8 8 ||11 11 |0 0 ||||12 12 |||0 0 |||5 5 |||0 0 ||5 5 ||||||8 ||||||||||||0 0 |12 12 |5 5 5 ||0 0 |||12 12 ||||||0 0 |0 0 |0 0 ||||0 0 ||0 0 ||||0 0 ||10 10 ||12 12 |12 12 ||0 0 |||||0 0 |||0 0 |||9 9 |0 0 |11 11 |0 0 |0 0 ||0 0 |||0 0 |11 11 |||0 0 ||||||||0 0 ||||||1 1 ||||||1 |||9 9 ||0 0 |||0 0 ||5 5 5 5 ||||0 0 |||0 0 ||||||0 0 |||||0 0 ||12 12 |||0 0 ||12 12 |12 12 |0 0 |0 0 ||0 0 ||0 0 |||||9 9 |0 0 |||0 0 |0 0 |9 9 |||||5 5 5 ||0 0 |0 0 ||0 0 |||0 0 ||||12 12 ||||||0 0 |||0 0 |0 0 ||0 0 ||||||||0 0 ||0 0 |0 0 |11 11 ||10 10 |0 0 |0 0 |0 0 |8 8 8 |||8 8 |0 0 |||12 12 |||||12 12 |8 8 8 8 8 |0 0 |0 0 |0 0 |0 0 |0 0 ||8 8 |||||||0 0 |||0 0 |8 8 ||0 0 |0 0 |||0 0 ||12 12 |10 10 |12 12 |||0 0 |8 8 ||0 0 ||0 0 ||1 1 1 1 ||8 8 |0 0 ||0 0 |0 0 ||0 0 |||8 8 |0 0 |0 0 |0 0 |0 0 ||1 1 1 1 1 1 |||0 0 |0 0 ||||0 0 |||0 0 |||||0 0 |||||0 0 |||0 0 |5 |0 0 |0 0 |10 10 ||0 0 |0 0 |12 12 ||12 12 |||||0 0 |12 12 ||0 0 |||0 0 |

||8 |9 ||0 0 |11 11 ||9 ||||0 0 ||9 ||||||12 12 |8 |5 5 5 ||||||8 8 |0 0 ||||9 9 |9 9 ||||5 5 |12 12 ||0 0 |5 5 5 5 |||||0 0 |0 0 ||12 12 ||0 0 |||8 8 8 ||12 12 ||||||0 0 |||||0 0 ||0 0 ||||0 0 |||||||9 9 ||10 10 |8 ||11 11 ||0 0 ||0 0 ||9 9 |0 0 ||||||||||0 0 ||12 12 |||8 |8 8 |||8 8 ||12 12 ||0 0 |10 10 |12 12 |0 0 |0 0 |0 0 |||8 8 |12 12 |12 12 |||||0 0 ||5 ||0 0 |0 0 ||0 0 |||0 0 ||12 12 |9 ||0 0 ||0 0 |0 0 |||12 12 ||0 0 ||0 0 |5 |||0 0 |||0 0 |||0 0 ||0 0 |0 0 |5 ||12 12 |12 12 |0 0 ||0 0 ||0 0 |12 12 ||9 |12 12 |0 0 |12 12 |||0 0 |0 0 |12 12 |12 12 ||0 0 |||||0 0 |0 0 ||||0 0 |12 12 |||0 0 |0 0 |||0 0 ||||0 0 |||8 |12 12 |0 0 |12 12 ||0 0 |0 0 |0 0 |0 0 ||0 0 |11 11 |||0 0 ||0 0 |||10 10 |0 0 ||12 12 ||9 |||0 0 ||10 10 |11 11 ||12 12 |||5 |0 0 ||5 |||0 0 |12 12 |12 12 |11 11 |||||0 0 |0 0 ||8 |||0 0 |5 |||9 |9 |0 0 ||0 0 |||0 0 ||8 8 |8 |9 |12 12 |12 12 |12 12 |||0 0 |8 8 |||||12 12 ||10 10 |||9 ||||12 12 ||5 |9 |0 0 ||9 ||10 10 |12 12 |12 12 |||0 0 |||0 0 |0 0 |||5 |||0 0 |0 0 

||||||||||||||5 ||9 |12 12 |||0 0 |9 |0 0 |5 ||0 0 ||0 0 ||||0 0 ||5 |0 0 |9 |0 0 |||||5 |||12 12 |0 0 ||12 12 |9 |9 |||||5 ||12 12 |12 12 |9 ||||12 12 |8 |12 12 ||||9 ||5 ||9 |||0 0 |||0 0 ||9 |0 0 |0 0 |||12 12 |0 0 |||||0 0 |0 0 ||9 ||12 12 |0 0 |9 |||0 0 |||||5 |||0 0 |9 ||5 |0 0 |5 |9 |9 ||||12 12 |9 |8 |5 |5 |9 |12 12 |5 |0 0 |0 0 |||0 0 |0 0 ||12 12 |8 |12 12 |12 12 |5 ||5 |5 ||||||5 |5 |9 ||5 |5 |9 ||||||0 0 |0 0 |9 |8 |8 |1 ||9 |9 |9 |||9 |0 0 |5 |9 ||||0 0 ||12 12 |5 |5 |9 |5 |5 |12 12 |12 12 ||5 ||9 |5 ||0 0 |||0 0 |5 ||0 0 |0 0 ||0 0 ||9 9 ||5 |||0 0 |12 12 |0 0 |12 12 |0 0 |0 0 ||0 0 |||5 ||5 |||0 0 ||5 |9 ||5 |5 |0 0 ||0 0 ||1 1 |||12 12 |0 0 ||0 0 ||9 |5 ||0 0 ||9 |5 ||0 0 |12 12 ||12 12 ||||9 |9 |9 |9 ||||9 ||||0 0 |0 0 ||0 0 |||||12 12 ||12 12 ||0 0 |0 0 |0 0 ||9 |9 |9 |5 |0 0 |9 |||||||9 ||||||9 |12 12 |0 0 |12 12 ||10 10 |||||||0 0 ||0 0 |0 0 ||||8 |0 0 |0 0 |8 8 |||9 ||5 ||0 0 |0 0 |||9 ||0 0 ||0 0 |||0 0 |9 ||12 12 |||||12 12 ||

|||||||||||||||||||||||||||||||||||

['17', 'Private', '269430', '10th', '6', 'Never-married', 'Machine-op-inspct', 'Not-in-family', 'White', 'Male', '0', '0', '40', 'United-States', '<=50K']
time: 0.12604451179504395 s
acc: 75.75757575757575 %
进度: 0.21248339973439576 %
['20', 'Private', '257509', 'HS-grad', '9', 'Never-married', 'Craft-repair', 'Own-child', 'White', 'Male', '0', '0', '40', 'United-States', '<=50K']
time: 0.17251992225646973 s
acc: 76.47058823529412 %
进度: 0.21912350597609562 %
['65', 'Private', '136384', 'Masters', '14', 'Married-civ-spouse', 'Prof-specialty', 'Husband', 'White', 'Male', '0', '0', '50', 'United-States', '>50K']
time: 0.12703824043273926 s
acc: 77.14285714285715 %
进度: 0.22576361221779548 %
['44', 'Self-emp-inc', '120277', 'Assoc-voc', '11', 'Married-civ-spouse', 'Sales', 'Husband', 'White', 'Male', '0', '0', '45', 'United-States', '>50K']
time: 0.16651320457458496 s
acc: 75.0 %
进度: 0.23240371845949534 %
['36', 'Private', '465326', 'HS-grad', '9', 'Married-civ-spouse', 'Farming-fishing', 'H

...

['37', 'Private', '210830', 'Assoc-voc', '11', 'Divorced', 'Prof-specialty', 'Unmarried', 'White', 'Female', '0', '0', '38', 'United-States', '<=50K']
time: 0.17851805686950684 s
acc: 75.49131397142665 %
进度: 98.99070385126161 %
['24', 'Private', '194848', 'Bachelors', '13', 'Never-married', 'Tech-support', 'Own-child', 'White', 'Male', '0', '0', '40', 'United-States', '<=50K']
time: 0.1266486644744873 s
acc: 75.49295774647888 %
进度: 98.99734395750332 %
['39', 'Private', '109351', 'Assoc-voc', '11', 'Separated', 'Adm-clerical', 'Not-in-family', 'White', 'Female', '0', '0', '40', 'United-States', '<=50K']
time: 0.17810487747192383 s
acc: 75.49460130105291 %
进度: 99.00398406374502 %
['39', 'Private', '105813', 'HS-grad', '9', 'Married-civ-spouse', 'Craft-repair', 'Husband', 'White', 'Male', '3908', '0', '72', 'United-States', '<=50K']
time: 0.12802433967590332 s
acc: 75.49624463519314 %
进度: 99.01062416998673 %
['32', 'Private', '123430', 'HS-grad', '9', 'Married-civ-spouse', 'Farming-fishin

['26', 'Private', '143280', 'HS-grad', '9', 'Never-married', 'Adm-clerical', 'Other-relative', 'White', 'Female', '0', '0', '40', 'United-States', '<=50K']
time: 0.1705179214477539 s
acc: 75.49013047842088 %
进度: 99.22974767596281 %
['41', 'Private', '242804', 'HS-grad', '9', 'Married-civ-spouse', 'Transport-moving', 'Husband', 'White', 'Male', '0', '0', '40', 'United-States', '>50K']
time: 0.12204146385192871 s
acc: 75.4850796199652 %
进度: 99.23638778220452 %
['48', 'Private', '156926', 'Bachelors', '13', 'Married-civ-spouse', 'Sales', 'Husband', 'White', 'Male', '0', '0', '45', 'United-States', '>50K']
time: 0.17051482200622559 s
acc: 75.48002943734528 %
进度: 99.24302788844622 %
['55', 'Self-emp-inc', '103948', 'Assoc-voc', '11', 'Married-civ-spouse', 'Exec-managerial', 'Husband', 'White', 'Male', '0', '0', '60', 'United-States', '<=50K']
time: 0.12833881378173828 s
acc: 75.47497993042548 %
进度: 99.24966799468791 %
['28', 'Private', '249720', 'Some-college', '10', 'Married-civ-spouse', '

['33', 'Self-emp-not-inc', '202153', 'Some-college', '10', 'Married-civ-spouse', 'Craft-repair', 'Husband', 'White', 'Male', '2829', '0', '40', 'United-States', '<=50K']
time: 0.16908860206604004 s
acc: 75.46892730792337 %
进度: 99.46879150066401 %
['35', 'Private', '238980', 'Some-college', '10', 'Never-married', 'Sales', 'Not-in-family', 'White', 'Male', '0', '0', '40', 'United-States', '<=50K']
time: 0.1242983341217041 s
acc: 75.47056467761314 %
进度: 99.47543160690572 %
['56', 'Self-emp-not-inc', '156873', 'HS-grad', '9', 'Married-civ-spouse', 'Craft-repair', 'Husband', 'White', 'Male', '0', '0', '40', 'United-States', '<=50K']
time: 0.1700267791748047 s
acc: 75.47220182873924 %
进度: 99.4820717131474 %
['20', 'Private', '32805', 'HS-grad', '9', 'Never-married', 'Other-service', 'Not-in-family', 'White', 'Female', '0', '0', '40', 'United-States', '<=50K']
time: 0.12251520156860352 s
acc: 75.47383876134543 %
进度: 99.48871181938911 %
['68', 'Self-emp-not-inc', '273088', 'Some-college', '10'

['29', 'Local-gov', '170482', 'HS-grad', '9', 'Married-civ-spouse', 'Protective-serv', 'Husband', 'Black', 'Male', '0', '2057', '40', 'United-States', '<=50K']
time: 0.1660463809967041 s
acc: 75.44782579742957 %
进度: 99.70783532536521 %
['34', 'Private', '113688', 'Some-college', '10', 'Divorced', 'Other-service', 'Not-in-family', 'White', 'Female', '0', '0', '34', 'United-States', '<=50K']
time: 0.12451696395874023 s
acc: 75.44946064722333 %
进度: 99.7144754316069 %
['27', 'Private', '133770', 'Bachelors', '13', 'Never-married', 'Prof-specialty', 'Not-in-family', 'Asian-Pac-Islander', 'Male', '2202', '0', '52', 'Philippines', '<=50K']
time: 0.16803503036499023 s
acc: 75.45109527931288 %
进度: 99.7211155378486 %
['57', 'Private', '161964', '12th', '8', 'Married-civ-spouse', 'Craft-repair', 'Husband', 'White', 'Male', '0', '0', '40', 'United-States', '<=50K']
time: 0.17864060401916504 s
acc: 75.45272969374169 %
进度: 99.72775564409031 %
['30', 'Private', '34572', 'Prof-school', '15', 'Married-

['31', 'Private', '440129', 'HS-grad', '9', 'Married-civ-spouse', 'Craft-repair', 'Husband', 'White', 'Male', '0', '0', '40', 'United-States', '<=50K']
time: 0.1626431941986084 s
acc: 75.4733275758985 %
进度: 99.9468791500664 %
['25', 'Private', '350977', 'HS-grad', '9', 'Never-married', 'Other-service', 'Own-child', 'White', 'Female', '0', '0', '40', 'United-States', '<=50K']
time: 0.17602968215942383 s
acc: 75.47495682210709 %
进度: 99.9535192563081 %
['48', 'Local-gov', '349230', 'Masters', '14', 'Divorced', 'Other-service', 'Not-in-family', 'White', 'Male', '0', '0', '40', 'United-States', '<=50K']
time: 0.12217402458190918 s
acc: 75.47658585187645 %
进度: 99.9601593625498 %
['33', 'Private', '245211', 'Bachelors', '13', 'Never-married', 'Prof-specialty', 'Own-child', 'White', 'Male', '0', '0', '40', 'United-States', '<=50K']
time: 0.17703747749328613 s
acc: 75.47821466524974 %
进度: 99.9667994687915 %
['39', 'Private', '215419', 'Bachelors', '13', 'Divorced', 'Prof-specialty', 'Not-in-fam

In [13]:
# 树的子节点使用列表存储，寻找时需要遍历，可能会影响速度
print('所用时间:',time_sum,'s')

所用时间: 2285.652803182602 s
